In [1]:
import tensorflow as tf
import pandas as pd
import tensorflow_hub as hub
import os
import re
import numpy as np
from bert.tokenization import FullTokenizer
#from tqdm import tqdm_notebook
from tensorflow.keras import backend as K

# Initialize session
sess = tf.Session()

# Params for bert model and tokenization

bert_path ="https://tfhub.dev/google/bert_uncased_L-12_H-768_A-12/1"

vocab_file = 'C:/Users/Aytu/python notebooks/NLP/model_bert/uncased_L-12_H-768_A-12/vocab.txt'
#BERT_INIT_CHKPNT = 'C:/Users/Aytu/python notebooks/bert_google/cased_L-12_H-768_A-12/cased_L-12_H-768_A-12/bert_model.ckpt'
#BERT_CONFIG = 'C:/Users/Aytu/python notebooks/bert_google/cased_L-12_H-768_A-12/cased_L-12_H-768_A-12/bert_config.json'

max_seq_length = 200

W0714 14:03:53.413147 15748 __init__.py:56] Some hub symbols are not available because TensorFlow version is less than 1.14


# Data

Using Cleaned data from previous studies about wikipedia

In [2]:
train = pd.read_csv('train_transformed_full.csv')
train=train[:
           ]
test = pd.read_csv('train_val_transformed_full.csv')
test=test[:
         ]

train.drop('Unnamed: 0',axis='columns',inplace=True)
#train.drop('comment_text',axis='columns',inplace=True)
cols=['id','transformed','comment_text','toxic','severe_toxic','obscene','threat','insult','identity_hate']
train=train[cols]

test.drop('Unnamed: 0',axis='columns',inplace=True)
#test.drop('comment_text',axis='columns',inplace=True)
cols=['id','transformed','comment_text','toxic','severe_toxic','obscene','threat','insult','identity_hate']
test=test[cols]

train=train.dropna(axis='rows')
test=test.dropna(axis='rows')
#train = pd.read_csv('train.csv')
#train=train[:50000]
#test = pd.read_csv('test.csv')
#test=test[:50000]

In [64]:
# Create datasets (Only take up to max_seq_length words for memory)
train_text = train['transformed'].tolist()
#train_text = [' '.join(t.split()[0:max_seq_length]) for t in train_text]
#train_text = np.array(train_text, dtype=object)[:, np.newaxis]
train_label = train['toxic'].tolist()

test_text = test['transformed'].tolist()
#test_text = [' '.join(t.split()[0:max_seq_length]) for t in test_text]
#test_text = np.array(test_text, dtype=object)[:, np.newaxis]
test_label = test['toxic'].tolist()

# Tokenize

Next, tokenize our text to create `input_ids`, `input_masks`, and `segment_ids`

Initially tokenized via Keras tokenizer and inserted special tokens, and did the padding


In [65]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from bert import tokenization
#tokenization.validate_case_matches_checkpoint(True,BERT_INIT_CHKPNT)
tokenizer = tokenization.FullTokenizer(
      vocab_file=vocab_file, do_lower_case=True)
#tokenizer_keras = FullTokenizer(vocab_file=vocab_file)

#Updates internal vocabulary based on a list of texts. This method creates the vocabulary index based on word frequency. 
#tokenizer_keras.fit_on_texts((train_text)) 

In [66]:
aa=[tokenizer.tokenize(text) for text in train_text]

In [67]:
bb=[tokenizer.convert_tokens_to_ids(tokens) for tokens in aa]

In [68]:
z=[row[:max_seq_length-2] for row in bb]

In [69]:
max([len(row) for row in z])

198

In [70]:
[row.insert(0,101) for row in z]
[row for row in z]

[[101,
  7526,
  2339,
  1996,
  10086,
  2191,
  2104,
  2026,
  5310,
  18442,
  13076,
  12392,
  2050,
  5470,
  2022,
  7065,
  8743,
  2027,
  2022,
  2025,
  3158,
  9305,
  22556,
  2074,
  8503,
  2006,
  2070,
  3806,
  2044,
  1045,
  3789,
  2012,
  2047,
  2259,
  10658,
  6904,
  2278,
  1998,
  3531,
  2079,
  2025,
  6366,
  1996,
  23561,
  2013,
  1996,
  2831,
  3931,
  2144,
  1045,
  2022,
  11036,
  2085],
 [101,
  4830,
  2860,
  2860,
  2002,
  2674,
  2023,
  4281,
  6120,
  1045,
  2022,
  9428,
  6293,
  2007,
  4067,
  2831,
  2254,
  11396],
 [101,
  4931,
  2158,
  1045,
  2022,
  2428,
  2025,
  3046,
  2000,
  10086,
  2162,
  2009,
  2022,
  2074,
  2008,
  2023,
  3124,
  2022,
  7887,
  6366,
  7882,
  2592,
  1998,
  2831,
  2000,
  2033,
  2083,
  10086,
  2612,
  1997,
  2026,
  2831,
  3931,
  2002,
  4025,
  2000,
  2729,
  2172,
  2055,
  1996,
  4289,
  2084,
  1996,
  5025,
  18558],
 [101,
  2172,
  1045,
  2064,
  2025,
  2191,
  2151,
  261

In [71]:
[row.append(102) for row in z]
[row for row in z]

[[101,
  7526,
  2339,
  1996,
  10086,
  2191,
  2104,
  2026,
  5310,
  18442,
  13076,
  12392,
  2050,
  5470,
  2022,
  7065,
  8743,
  2027,
  2022,
  2025,
  3158,
  9305,
  22556,
  2074,
  8503,
  2006,
  2070,
  3806,
  2044,
  1045,
  3789,
  2012,
  2047,
  2259,
  10658,
  6904,
  2278,
  1998,
  3531,
  2079,
  2025,
  6366,
  1996,
  23561,
  2013,
  1996,
  2831,
  3931,
  2144,
  1045,
  2022,
  11036,
  2085,
  102],
 [101,
  4830,
  2860,
  2860,
  2002,
  2674,
  2023,
  4281,
  6120,
  1045,
  2022,
  9428,
  6293,
  2007,
  4067,
  2831,
  2254,
  11396,
  102],
 [101,
  4931,
  2158,
  1045,
  2022,
  2428,
  2025,
  3046,
  2000,
  10086,
  2162,
  2009,
  2022,
  2074,
  2008,
  2023,
  3124,
  2022,
  7887,
  6366,
  7882,
  2592,
  1998,
  2831,
  2000,
  2033,
  2083,
  10086,
  2612,
  1997,
  2026,
  2831,
  3931,
  2002,
  4025,
  2000,
  2729,
  2172,
  2055,
  1996,
  4289,
  2084,
  1996,
  5025,
  18558,
  102],
 [101,
  2172,
  1045,
  2064,
  2025,


In [72]:

X_t = pad_sequences(z, maxlen=max_seq_length,padding='post')

In [73]:
X_t[4]

array([ 101, 2017, 2909, 2022, 2026, 5394, 2151, 3382, 2017, 3342, 2054,
       3931, 2008, 2022, 2006,  102,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,   

In [74]:
cc=[tokenizer.tokenize(text) for text in test_text]


dd=[tokenizer.convert_tokens_to_ids(tokens) for tokens in cc]


zz=[row[:max_seq_length-2] for row in dd]


max([len(row) for row in zz])


[row.insert(0,101) for row in zz]
[row for row in zz]

[[101,
  5043,
  3973,
  2006,
  1052,
  5070,
  2360,
  2008,
  2178,
  1997,
  1996,
  18414,
  29165,
  2012,
  1996,
  7987,
  2378,
  3600,
  9091,
  1999,
  15500,
  2022,
  1996,
  3525,
  2172,
  3297,
  6798,
  2030,
  12551,
  7570,
  24412,
  9072,
  11978,
  2015,
  28567,
  2153,
  3046,
  2000,
  17727,
  15916,
  2078,
  1996,
  6467,
  2015,
  2424,
  2011,
  4366,
  1996,
  6467,
  2022,
  5308,
  2007,
  4345,
  10129,
  5070,
  2022,
  1999,
  7561,
  2065,
  2017,
  2175,
  2000,
  1996,
  6254,
  2993,
  2006,
  2026,
  4773,
  13704,
  21677,
  2112,
  2026,
  24051,
  2202,
  2013,
  5070,
  2015,
  2219,
  24051,
  2265,
  2008,
  1996,
  18414,
  29165,
  2171,
  2022,
  2507,
  1999,
  3763,
  1037,
  13031,
  2072,
  4151,
  3619,
  9072,
  2094,
  1998,
  13031,
  2072,
  2022,
  2025,
  3763,
  2005,
  2593,
  6798,
  2030,
  12551,
  5070,
  2113,
  2440,
  2204,
  2008,
  1996,
  18414,
  29165,
  2171,
  2022,
  2025,
  6798,
  2030,
  12551,
  7570,
  2

In [75]:
[row.append(102) for row in zz]
[row for row in zz]

[[101,
  5043,
  3973,
  2006,
  1052,
  5070,
  2360,
  2008,
  2178,
  1997,
  1996,
  18414,
  29165,
  2012,
  1996,
  7987,
  2378,
  3600,
  9091,
  1999,
  15500,
  2022,
  1996,
  3525,
  2172,
  3297,
  6798,
  2030,
  12551,
  7570,
  24412,
  9072,
  11978,
  2015,
  28567,
  2153,
  3046,
  2000,
  17727,
  15916,
  2078,
  1996,
  6467,
  2015,
  2424,
  2011,
  4366,
  1996,
  6467,
  2022,
  5308,
  2007,
  4345,
  10129,
  5070,
  2022,
  1999,
  7561,
  2065,
  2017,
  2175,
  2000,
  1996,
  6254,
  2993,
  2006,
  2026,
  4773,
  13704,
  21677,
  2112,
  2026,
  24051,
  2202,
  2013,
  5070,
  2015,
  2219,
  24051,
  2265,
  2008,
  1996,
  18414,
  29165,
  2171,
  2022,
  2507,
  1999,
  3763,
  1037,
  13031,
  2072,
  4151,
  3619,
  9072,
  2094,
  1998,
  13031,
  2072,
  2022,
  2025,
  3763,
  2005,
  2593,
  6798,
  2030,
  12551,
  5070,
  2113,
  2440,
  2204,
  2008,
  1996,
  18414,
  29165,
  2171,
  2022,
  2025,
  6798,
  2030,
  12551,
  7570,
  2

In [76]:

X_test = pad_sequences(zz, maxlen=max_seq_length,padding='post')

In [77]:
segmentler_test=[]
maske_test=np.array([[1 if element>1 else 0 for element in row] for row in X_test])
segmentler_test = np.zeros(maske_test.shape).astype(int)
segmentler_test.fill(1)

In [78]:
from imblearn.over_sampling import ADASYN, SMOTE

""" Oversampling for threat label class. What smote does is simple. First it finds the n-nearest neighbors in the minority
class for each of the samples in the class. Then it draws a line between the the neighbors an generates random points
on the lines and adds a random small values to the points to increase variance in them."""

# First we count the prevalent class, and base our oversampling model on this number
count=len(train_label)-sum(train_label)
#count*0.01

#ADASYN model with class ratio dict 
sm = ADASYN(ratio={1: int(count*0.25), 0:int(count*1)},random_state=7)

X_t_sm, y_sm = sm.fit_sample(X_t, train_label)

# Resultant dataset changes in size
y_sm.shape
X_t_sm.shape

(142828, 200)

In [79]:
maskexx=np.array([min(np.where(row==0)) for row in X_t_sm])
maskexx=[row.min() if row.size!=0 else max_seq_length for row in maskexx] 
sh=X_t_sm.shape[0]
for n in range(sh-1):
    X_t_sm[n,maskexx[n]-1]=102

In [80]:
maske_sm=np.array([[1 if element>1 else 0 for element in row] for row in X_t_sm])
segmentler_sm = np.zeros(maske_sm.shape).astype(int)

In [81]:
segmentler_sm.fill(1)

In [82]:
maske=np.array([[1 if element>1 else 0 for element in row] for row in X_t])
segmentler = np.zeros(maske.shape).astype(int)
segmentler.fill(1)

In [83]:
class BertLayer(tf.layers.Layer):
    def __init__(
        self,
        n_fine_tune_layers=10,
        pooling="first",
        bert_path="https://tfhub.dev/google/bert_uncased_L-12_H-768_A-12/1",
        **kwargs,
    ):
        self.n_fine_tune_layers = n_fine_tune_layers
        self.trainable = True
        self.output_size = 768
        self.pooling = pooling
        self.bert_path = bert_path
        if self.pooling not in ["first", "mean"]:
            raise NameError(
                f"Undefined pooling type (must be either first or mean, but is {self.pooling}"
            )

        super(BertLayer, self).__init__(**kwargs)

    def build(self, input_shape):
        self.bert = hub.Module(
            self.bert_path,
            trainable=self.trainable, 
            name=f"{self.name}_module"
        )

########       # Remove unused layers
#######        trainable_vars = self.bert.variables
########       if self.pooling == "first":
#######        trainable_vars = [var for var in trainable_vars if not "/cls/" in var.name]
#######        trainable_layers = ["embeddings","pooler/dense"]
#######
########       elif self.pooling == "mean":
########           trainable_vars = [
########               var
########               for var in trainable_vars
########               if not "/cls/" in var.name and not "/pooler/" in var.name
########           ]
########           trainable_layers = []
########       else:
########           raise NameError(
########               f"Undefined pooling type (must be either first or mean, but is {self.pooling}"
########           )
#######
########       # Select how many layers to fine tune
#######        for i in range(self.n_fine_tune_layers):
#######           trainable_layers.append(f"encoder/layer_{str(10 - i)}")
#######
########       # Update trainable vars to contain only the specified layers
#######        trainable_vars = [var for var in trainable_vars
#######           if any([l in var.name for l in trainable_layers])
#######       ]
#######
########       # Add to trainable weights
#######        for var in trainable_vars:
#######           self._trainable_weights.append(var)
#######
#######        for var in self.bert.variables:
#######           if var not in self._trainable_weights:
#######               self._non_trainable_weights.append(var)
#######
        super(BertLayer, self).build(input_shape)

    def call(self, inputs):
        inputs = [K.cast(x, dtype="int32") for x in inputs]
        input_ids, input_mask, segment_ids = inputs
        bert_inputs = dict(
            input_ids=input_ids, input_mask=input_mask, segment_ids=segment_ids
        )
        if self.pooling == "first":
            pooled = self.bert(inputs=bert_inputs, signature="tokens", as_dict=True)[
                "pooled_output"
            ]
        elif self.pooling == "mean":
            result = self.bert(inputs=bert_inputs, signature="tokens", as_dict=True)[
                "sequence_output"
            ]

            mul_mask = lambda x, m: x * tf.expand_dims(m, axis=-1)
            masked_reduce_mean = lambda x, m: tf.reduce_sum(mul_mask(x, m), axis=1) / (
                    tf.reduce_sum(m, axis=1, keepdims=True) + 1e-10)
            input_mask = tf.cast(input_mask, tf.float32)
            pooled = masked_reduce_mean(result, input_mask)
        else:
            raise NameError(f"Undefined pooling type (must be either first or mean, but is {self.pooling}")

        return pooled

    def compute_output_shape(self, input_shape):
        return (input_shape[0], self.output_size)

In [84]:
def recall(y_true, y_pred):
        """Recall metric.

        Only computes a batch-wise average of recall.

        Computes the recall, a metric for multi-label classification of
        how many relevant items are selected.
        """
        true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
        possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
        recall1 = true_positives / (possible_positives + K.epsilon())
        return recall1

def precision(y_true, y_pred):
        """Precision metric.

        Only computes a batch-wise average of precision.

        Computes the precision, a metric for multi-label classification of
        how many selected items are relevant.
        """
        true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
        predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
        precision = true_positives / (predicted_positives + K.epsilon())
        return precision
    
    

def f1(y_true, y_pred):
    
    
    #precision1 = precision(y_true, y_pred)
    #recall1 = recall(y_true, y_pred)
    f1=2*((precision(y_true, y_pred)*recall(y_true, y_pred))/(precision(y_true, y_pred)\
                                                              +recall(y_true, y_pred)+K.epsilon()))
    return f1
    
from sklearn.metrics import roc_auc_score
#roc=roc_auc_score()


def auc(y_true, y_pred,average=None):
    K.get_session().run(K.local_variables_initializer())
    auc = roc_auc_score(y_true, y_pred)
    
    return auc
#model.compile(loss='binary_crossentropy',
#          optimizer= "adam",
#          metrics=[f1])

In [85]:
#from keras.layers import Embedding

# Build model
def build_model(max_seq_length): 
    in_id = tf.keras.layers.Input(shape=(max_seq_length,), name="input_ids")
    in_mask = tf.keras.layers.Input(shape=(max_seq_length,), name="input_masks")
    in_segment = tf.keras.layers.Input(shape=(max_seq_length,), name="segment_ids")
    
    #embed_size = 300
    #max_features = 20000
    #embed = Embedding(max_features, embed_size)(in_id)
    #in_mask = Embedding(max_features, embed_size)(in_mask)
    #in_segment = Embedding(max_features, embed_size)(in_segment)
    
    bert_inputs = [in_id, in_mask, in_segment]
    
    bert_output = BertLayer(n_fine_tune_layers=3, pooling="first")(bert_inputs)
    dense = tf.keras.layers.Dense(256, activation='relu')(bert_output)
   # dense = tf.keras.layers.Dense(128, activation='relu')(dense)
    pred = tf.keras.layers.Dense(1, activation='sigmoid')(dense)
    
    model = tf.keras.models.Model(inputs=bert_inputs, outputs=pred)
    
    #model.compile(loss='binary_crossentropy', optimizer=optimizer,metrics=['accuracy',recall,precision,f1])
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy',recall,precision,f1])
    model.summary()
    
    return model

def initialize_vars(sess):
    sess.run(tf.local_variables_initializer())
    sess.run(tf.global_variables_initializer())
    sess.run(tf.tables_initializer())
    K.set_session(sess)


In [86]:
train_labels=np.array(train_label)

In [87]:
from sklearn.utils import class_weight
class_weight = class_weight.compute_class_weight('balanced',np.unique(y_sm),y_sm)

#from sklearn.utils import class_weight
#class_weight = class_weight.compute_class_weight('balanced',np.unique(train_label),train_label)

In [88]:
from sklearn.utils import class_weight
class_weight = class_weight.compute_class_weight('balanced',np.unique(train_label),train_label)

#from sklearn.utils import class_weight
#class_weight = class_weight.compute_class_weight('balanced',np.unique(train_label),train_label)

In [89]:
class_weight

array([0.55309159, 5.20884388])

In [90]:
#from keras.callbacks import Callback
#from keras_tqdm import TQDMNotebookCallback
model = build_model(max_seq_length)

# Instantiate variables
initialize_vars(sess)



model.fit(
    [X_t, maske, segmentler],train_labels,
    # y_sm,
    #validation_data=([test_input_ids, test_input_masks, test_segment_ids], test_labels),
    validation_split=0.2,
    epochs=2,
    batch_size=128 , 
    verbose=1, 
    callbacks=None,
    class_weight=class_weight
)#callbacks=[TQDMNotebookCallback(leave_inner=False, leave_outer=True)]

INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I0714 21:41:04.896093 15748 saver.py:1483] Saver not created because there are no variables in the graph to restore


INFO:tensorflow:Saver not created because there are no variables in the graph to restore


I0714 21:41:07.984263 15748 saver.py:1483] Saver not created because there are no variables in the graph to restore


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_ids (InputLayer)          (None, 200)          0                                            
__________________________________________________________________________________________________
input_masks (InputLayer)        (None, 200)          0                                            
__________________________________________________________________________________________________
segment_ids (InputLayer)        (None, 200)          0                                            
__________________________________________________________________________________________________
bert_layer_5 (BertLayer)        (None, 768)          0           input_ids[0][0]                  
                                                                 input_masks[0][0]                
          

In [29]:
preds= model.predict([X_test, 
                                maske_test, 
                                segmentler_test]
                              ) # predictions after we clear and reload model

In [30]:
import  sklearn.metrics  as met

In [95]:
met.roc_auc_score(test_label,preds)

0.9462850733371103